In [1]:
import torch
from torch.utils.data import Dataset
import json
import os
import torch.nn as nn
import torch.nn.functional as func
from torch.utils.data import DataLoader
import torch.optim as optim
from os.path import expanduser
import splitfolders
import shutil
import glob
import numpy as np
from sklearn.model_selection import train_test_split

device = 'cuda' if torch.cuda.is_available() else 'cpu'
# torch.cuda.set_per_process_memory_fraction(0.9, 0)
print(device)

cuda


In [2]:
class KpVelDataset(Dataset):
    def __init__(self, json_folder):
        super(KpVelDataset, self).__init__()
        self.data = []
        for json_file in sorted(os.listdir(json_folder)):
            if json_file.endswith('_combined.json'):
                with open(os.path.join(json_folder, json_file), 'r') as file:
                    data = json.load(file)
                    start_kp = data['start_kp']
                    next_kp = data['next_kp']
                    position = data['position']
                    self.data.append((start_kp, next_kp, position))

#     def __init__(self, json_folder):
#         super(KpVelDataset, self).__init__()
#         self.data = []
#         for json_file in sorted(os.listdir(json_folder)):
#             if json_file.endswith('_combined.json'):
#                 with open(os.path.join(json_folder, json_file), 'r') as file:
#                     data = json.load(file)
#                     # Ensure data contains 'start_kp', 'next_kp', and 'position'
#                     if 'start_kp' in data and 'next_kp' in data and 'position' in data:
#                         start_kp = data['start_kp']
#                         next_kp = data['next_kp']
#                         position = data['position']
#                         # Only append if start_kp and next_kp are not empty
#                         if start_kp and next_kp:
#                             self.data.append((start_kp, next_kp, position))

    def __len__(self):
        return len(self.data)

    def __getitem__(self, idx):
        start_kp, next_kp, position = self.data[idx]
        # Ensure start_kp and next_kp have consistent dimensions
#         if not start_kp or not next_kp:
#             raise ValueError(f"Empty keypoints found at index {idx}")
        start_kp_flat = torch.tensor([kp for sublist in start_kp for kp in sublist[0][:2]], dtype=torch.float)
        next_kp_flat = torch.tensor([kp for sublist in next_kp for kp in sublist[0][:2]], dtype=torch.float)
        position = torch.tensor(position, dtype=torch.float)
        return start_kp_flat, next_kp_flat, position

#     def __len__(self):
#         return len(self.data)

# #     def __getitem__(self, idx):
# #         start_kp, next_kp, velocity = self.data[idx]
# #         start_kp_flat = torch.tensor([kp for sublist in start_kp for kp in sublist[0]])
# #         next_kp_flat = torch.tensor([kp for sublist in next_kp for kp in sublist[0]])
# #         velocity = torch.tensor(velocity)
# #         return start_kp_flat, next_kp_flat, velocity
  
#     def __getitem__(self, idx):
#         start_kp, next_kp, position = self.data[idx]
#         # Extract and flatten the first two elements of each keypoint in start_kp
#         start_kp_flat = torch.tensor([kp for sublist in start_kp for kp in sublist[0][:2]], dtype=torch.float)
#         # Extract and flatten the first two elements of each keypoint in next_kp
#         next_kp_flat = torch.tensor([kp for sublist in next_kp for kp in sublist[0][:2]], dtype=torch.float)
#         position = torch.tensor(position)
#         return start_kp_flat, next_kp_flat, position
    

In [3]:
def train_test_split(src_dir):
#     dst_dir_img = src_dir + "images"
    dst_dir_anno = src_dir + "annotations"
    
    if os.path.exists(dst_dir_anno):
        print("folders exist")
    else:
        os.mkdir(dst_dir_anno)
        
#     for jpgfile in glob.iglob(os.path.join(src_dir, "*.jpg")):
#         shutil.copy(jpgfile, dst_dir_img)

    for jsonfile in glob.iglob(os.path.join(src_dir, "*_combined.json")):
        shutil.copy(jsonfile, dst_dir_anno)
        
    output = root_dir + "split_folder_reg"
    
    splitfolders.ratio(src_dir, # The location of dataset
                   output=output, # The output location
                   seed=42, # The number of seed
                   ratio=(0.8, 0.1, 0.1), # The ratio of split dataset
                   group_prefix=None, # If your dataset contains more than one file like ".jpg", ".pdf", etc
                   move=False # If you choose to move, turn this into True
                   )
    
#     shutil.rmtree(dst_dir_img)
    shutil.rmtree(dst_dir_anno)
    
    return output  

In [4]:
class PosRegModel(nn.Module):
    def __init__(self, input_size):
        super(PosRegModel, self).__init__()
        self.fc1 = nn.Linear(input_size * 2, 1024)  # Assuming start_kp and next_kp are concatenated
        self.fc2 = nn.Linear(1024, 512)
        self.fc3 = nn.Linear(512,256)
        self.fc4 = nn.Linear(256,128)
        self.fc5 = nn.Linear(128,64)
        self.fc6 = nn.Linear(64,64)
        self.fc7 = nn.Linear(64,3)  # Output size is 3 for velocity

    def forward(self, start_kp, next_kp):
        x = torch.cat((start_kp.to(device), next_kp.to(device)), dim=1)
        x = func.relu(self.fc1(x))
        x = func.relu(self.fc2(x))
        x = func.relu(self.fc3(x))
        x = func.relu(self.fc4(x))
        x = func.relu(self.fc5(x))
        x = func.relu(self.fc6(x))
        x = self.fc7(x)
        return x
    

In [17]:
# Initialize dataset and data loader
# to generalize home directory. User can change their parent path without entering their home directory
num_epochs = 300
batch_size = 64
v = 1
root_dir = '/home/jc-merlab/Pictures/panda_data/panda_sim_vel/regression_combined_test_new/'
print(root_dir)
split_folder_path = train_test_split(root_dir)
dataset = KpVelDataset(root_dir)
data_loader = DataLoader(dataset, batch_size=batch_size, shuffle=True)

# Initialize model
model = PosRegModel(12)  # Adjust input_size as necessary
model = model.to(device)
criterion = nn.MSELoss()
optimizer = optim.Adam(model.parameters(), lr=0.005)

# Training loop
for epoch in range(num_epochs):
    for start_kp, next_kp, position in data_loader:
        optimizer.zero_grad()
        position = position.squeeze(1)
        print(position)
        print(start_kp.shape)
        print(position.shape)
        output = model(start_kp, next_kp)
        loss = criterion(output, position.to(device))
        loss.backward()
        optimizer.step()
        print("output", output)
    print(f'Epoch {epoch+1}, Loss: {loss.item()}')
    
# # Save the trained model
model_save_path = f'/home/jc-merlab/Pictures/Data/trained_models/reg_pos_b{batch_size}_e{num_epochs}_v{v}.pth'
torch.save(model.state_dict(), model_save_path)

# model_save_path = f'/home/jc-merlab/Pictures/Data/trained_models/reg_nkp_b{batch_size}_e{num_epochs}_v{v}.pth'
# torch.save({
#     'model_state_dict': model.state_dict(),
#     'model_structure': KeypointRegressionNet()
# }, model_save_path)
# print(f"Model saved to {model_save_path}")


/home/jc-merlab/Pictures/panda_data/panda_sim_vel/regression_combined_test_new/


Copying files: 12428 files [00:00, 21412.15 files/s]


tensor([[ 0.0000, -0.0032,  0.0000],
        [ 0.0000,  0.0000, -0.0100],
        [-0.0098,  0.0000,  0.0000],
        [ 0.0000,  0.0709,  0.5500],
        [-0.4024, -0.1385, -0.2000],
        [ 0.0000, -0.0419, -0.3400],
        [ 0.0000,  0.0000,  0.0100],
        [ 0.0000,  0.0000,  0.0100],
        [-0.0098,  0.0000,  0.0000],
        [ 0.0000,  0.0016,  0.0000],
        [ 0.2879,  0.0236,  0.3500],
        [ 0.0000, -0.0016,  0.0000],
        [ 0.0000,  0.0000,  0.0100],
        [ 0.0000,  0.0000,  0.0100],
        [ 0.0000,  0.0000, -0.0100],
        [ 0.0000,  0.0000, -0.0100],
        [ 0.0000,  0.0000, -0.0100],
        [ 0.0000, -0.0043,  0.0000],
        [ 0.0000,  0.0000, -0.0100],
        [ 0.0000,  0.0000,  0.0100],
        [ 0.3730,  0.1514,  0.3600],
        [ 0.0000,  0.0000,  0.0100],
        [ 0.0000, -0.0021,  0.0000],
        [ 0.0065,  0.0000,  0.0000],
        [ 0.0000,  0.0032,  0.0000],
        [ 0.0000, -0.0021,  0.0000],
        [ 0.0000,  0.0000, -0.0100],
 

output tensor([[ 3.1522e-02, -1.3716e-02, -4.6788e-03],
        [ 1.1892e-02, -2.8638e-03,  3.2473e-03],
        [ 3.0291e-02, -1.4094e-02, -4.3356e-03],
        [ 3.0887e-02, -1.4706e-02, -2.6313e-03],
        [ 3.0474e-02, -1.0721e-02,  1.8433e-04],
        [ 2.5711e-02, -4.4835e-03,  4.2173e-03],
        [ 1.9965e-02, -4.9533e-03,  8.8155e-05],
        [ 2.2647e-02, -2.5438e-03,  4.4529e-03],
        [ 2.0134e-02, -3.5742e-03,  2.9258e-03],
        [ 2.0928e-02, -3.2394e-03,  2.5421e-03],
        [ 3.1788e-02, -1.4403e-02, -2.0833e-03],
        [ 1.1818e-02, -2.5361e-03,  3.8691e-03],
        [ 1.3715e-02, -4.6640e-03,  2.4978e-03],
        [ 2.3386e-02, -1.1075e-02, -1.1308e-02],
        [ 2.9966e-02, -1.4131e-02, -1.0034e-02],
        [ 1.8077e-02, -8.7129e-03, -1.2639e-03],
        [ 1.1871e-02, -2.3445e-03,  4.1836e-03],
        [ 3.1307e-02, -1.4204e-02, -8.9516e-03],
        [ 3.0267e-02, -1.4234e-02, -4.8118e-03],
        [ 3.2034e-02, -1.3497e-02, -2.6511e-03],
        [ 3.0

tensor([[ 0.0000,  0.0000,  0.0100],
        [ 0.0049,  0.0000,  0.0000],
        [ 0.0000, -0.0548, -0.3600],
        [ 0.0000,  0.0021,  0.0000],
        [ 0.0000,  0.0000, -0.0100],
        [ 0.0000,  0.1369, -0.0300],
        [ 0.0000,  0.0021,  0.0000],
        [ 0.0000,  0.0000, -0.1100],
        [ 0.0065,  0.0000,  0.0000],
        [ 0.0000,  0.0000,  0.0100],
        [ 0.0000,  0.0000,  0.0100],
        [ 0.0000,  0.0000,  0.0100],
        [ 0.0000,  0.0000,  0.0100],
        [ 0.0000,  0.0000,  0.0100],
        [ 0.0000,  0.0000,  0.0100],
        [-0.2846, -0.1417, -0.8800],
        [ 0.0000,  0.0000, -0.0100],
        [ 0.0000, -0.0016,  0.0000],
        [ 0.0000,  0.0000, -0.0100],
        [ 0.0000,  0.0016,  0.0000],
        [ 0.0000,  0.0000,  0.0100],
        [ 0.0000,  0.0000, -0.0100],
        [ 0.0000,  0.0000, -0.0100],
        [ 0.0000,  0.1578,  0.0400],
        [ 0.0000,  0.0215,  0.0000],
        [ 0.0000, -0.0032,  0.0000],
        [ 0.0000, -0.0016,  0.0000],
 

...

output tensor([[-2.7267e-03,  8.8168e-03, -3.6276e-03],
        [ 2.5188e-03,  6.8457e-03, -7.8214e-03],
        [-1.1937e-02,  6.8672e-03, -3.9689e-03],
        [ 4.6532e-03,  5.3220e-03, -1.0507e-02],
        [-3.2105e-03,  8.5865e-03, -3.7525e-03],
        [ 2.6594e-03,  7.0956e-03, -7.5082e-03],
        [ 7.8500e-04,  7.2066e-03, -6.9662e-03],
        [ 3.2708e-04,  6.2966e-03, -6.6068e-03],
        [ 6.8375e-04,  6.9005e-03, -8.3370e-03],
        [ 2.2497e-03,  6.9282e-03, -8.8117e-03],
        [-8.1970e-03,  7.0326e-03, -4.9798e-03],
        [ 5.1579e-03,  6.2981e-03, -9.6919e-03],
        [ 1.1173e-03,  7.1733e-03, -7.9820e-03],
        [ 2.4708e-04,  8.1938e-03, -5.5018e-03],
        [ 1.2370e-03,  7.2755e-03, -7.1089e-03],
        [ 4.0551e-03,  6.5326e-03, -9.9626e-03],
        [-2.5494e-04,  7.6011e-03, -6.3374e-03],
        [-1.9089e-03,  7.1635e-03, -6.6229e-03],
        [-2.1737e-04,  8.2667e-03, -5.6577e-03],
        [ 3.3798e-03,  4.6031e-03, -9.6683e-03],
        [ 4.2

output tensor([[ 1.6868e-03,  1.8151e-06,  8.2559e-03],
        [ 1.2031e-03,  1.8737e-03,  1.1205e-02],
        [ 7.5269e-05,  3.6823e-04,  9.4642e-03],
        [-6.3067e-03,  2.6513e-04,  1.3414e-02],
        [-7.8788e-04,  1.0214e-03,  1.1158e-02],
        [-9.3035e-03,  1.2506e-03,  1.7094e-02],
        [-8.9024e-03,  1.3484e-03,  1.6915e-02],
        [-1.2254e-02,  7.8173e-04,  1.8515e-02],
        [-5.0055e-03,  1.5261e-03,  1.4694e-02],
        [-1.0016e-03,  1.9936e-03,  1.2932e-02],
        [ 4.7579e-04, -1.3185e-03,  6.9997e-03],
        [-1.2887e-04,  3.3339e-03,  1.2924e-02],
        [ 7.3012e-04,  1.6653e-03,  1.1288e-02],
        [-1.2502e-02,  7.5016e-04,  1.8934e-02],
        [ 2.7699e-04, -1.2622e-03,  7.2768e-03],
        [-4.9314e-04,  2.8682e-03,  1.3539e-02],
        [ 1.2969e-03,  1.1088e-04,  8.1931e-03],
        [-2.5932e-03,  2.5648e-03,  1.4631e-02],
        [ 8.0056e-04,  2.1148e-04,  9.1328e-03],
        [-1.7696e-02,  6.1627e-04,  2.3758e-02],
        [ 1.3

output tensor([[ 2.4262e-03,  2.5224e-03,  2.9429e-03],
        [ 2.7775e-03,  2.0914e-03,  2.4646e-03],
        [ 1.4671e-03,  2.8406e-03,  3.7799e-03],
        [-1.5141e-02,  3.9748e-04,  1.0987e-02],
        [-1.1001e-03,  4.0975e-03,  5.7768e-03],
        [ 1.9982e-04,  3.5292e-03,  4.9101e-03],
        [-4.5745e-03,  5.2199e-03,  8.4377e-03],
        [ 2.9566e-04,  2.4918e-03,  4.5980e-03],
        [-5.7011e-03,  5.1897e-03,  9.4923e-03],
        [-3.4819e-03,  1.9295e-03,  6.7914e-03],
        [ 1.9341e-04,  4.1109e-03,  4.9061e-03],
        [ 9.2164e-04,  1.9765e-03,  3.6969e-03],
        [ 3.8697e-04,  3.4288e-03,  4.1889e-03],
        [-3.0592e-03,  6.0161e-03,  7.1153e-03],
        [-2.7712e-03,  3.3960e-03,  7.1103e-03],
        [ 8.5924e-05,  3.5263e-03,  4.9939e-03],
        [ 1.4659e-03,  1.9412e-03,  3.4391e-03],
        [-4.7250e-03,  5.1220e-03,  8.6156e-03],
        [-2.8961e-02, -1.3801e-03,  1.8367e-02],
        [-7.5090e-03,  8.4543e-04,  7.2509e-03],
        [-5.2

output tensor([[-0.0174,  0.0050,  0.0112],
        [-0.0230,  0.0041,  0.0121],
        [-0.0231,  0.0075,  0.0160],
        [-0.0158,  0.0050,  0.0101],
        [-0.0172,  0.0052,  0.0106],
        [-0.0218,  0.0073,  0.0152],
        [-0.0187,  0.0062,  0.0128],
        [-0.0178,  0.0006,  0.0047],
        [-0.0177,  0.0041,  0.0099],
        [-0.0158,  0.0056,  0.0109],
        [-0.0372,  0.0039,  0.0198],
        [-0.0169,  0.0044,  0.0094],
        [-0.0167,  0.0038,  0.0084],
        [-0.0136,  0.0031,  0.0066],
        [-0.0229,  0.0041,  0.0121],
        [-0.0133,  0.0046,  0.0085],
        [-0.0181,  0.0027,  0.0079],
        [-0.0227,  0.0074,  0.0157],
        [-0.0113,  0.0056,  0.0083],
        [-0.0227,  0.0041,  0.0120],
        [-0.0147,  0.0036,  0.0074],
        [-0.0198,  0.0068,  0.0137],
        [-0.0139,  0.0037,  0.0071],
        [-0.0172,  0.0044,  0.0095],
        [-0.0264,  0.0079,  0.0177],
        [-0.0182,  0.0065,  0.0128],
        [-0.0263,  0.0036,  0.0

KeyboardInterrupt: 

In [8]:
def test_model(model_path, test_data_dir):
    # Load the test dataset
    test_dataset = KpVelDataset(test_data_dir)
    test_loader = DataLoader(test_dataset, batch_size=32, shuffle=False)

    # Initialize the model and load the saved state
    model = PosRegModel(12)    
    model.load_state_dict(torch.load(model_path))
    model.to(device)
    model.eval()

    # Criterion for evaluation
    criterion = nn.MSELoss()
    total_loss = 0

    # No gradient needed for evaluation
    with torch.no_grad():
        for start_kp, next_kp, position in test_loader:
            output = model(start_kp.to(device), next_kp.to(device))
            for i in range(start_kp.size(0)):
                individual_start_kp = start_kp[i]
                individual_next_kp = next_kp[i]
                individual_position = position[i]
                predicted_position = output[i]

                print("Start KP:", individual_start_kp)
                print("Next KP:", individual_next_kp)
                print("Actual Position:", individual_position)
                print("Predicted Position:", predicted_position)
                print("-----------------------------------------")
            loss = criterion(output, predicted_position)
            total_loss += loss.item()
            
    # Calculate the average loss
    avg_loss = total_loss / len(test_loader)
    print(f'Average Test Loss: {avg_loss}')

# Usage
model_path = '/home/jc-merlab/Pictures/Data/trained_models/reg_pos_b32_e200_v1.pth'  # Update with your model path
test_data_dir = '/home/jc-merlab/Pictures/panda_data/panda_sim_vel/regression_combined_test_new/split_folder_reg/test/annotations/'  # Update with your test data path
test_model(model_path, test_data_dir)

RuntimeError: Error(s) in loading state_dict for PosRegModel:
	Missing key(s) in state_dict: "fc5.weight", "fc5.bias", "fc6.weight", "fc6.bias", "fc7.weight", "fc7.bias". 
	size mismatch for fc1.weight: copying a param with shape torch.Size([256, 24]) from checkpoint, the shape in current model is torch.Size([1024, 24]).
	size mismatch for fc1.bias: copying a param with shape torch.Size([256]) from checkpoint, the shape in current model is torch.Size([1024]).
	size mismatch for fc2.weight: copying a param with shape torch.Size([128, 256]) from checkpoint, the shape in current model is torch.Size([512, 1024]).
	size mismatch for fc2.bias: copying a param with shape torch.Size([128]) from checkpoint, the shape in current model is torch.Size([512]).
	size mismatch for fc3.weight: copying a param with shape torch.Size([64, 128]) from checkpoint, the shape in current model is torch.Size([256, 512]).
	size mismatch for fc3.bias: copying a param with shape torch.Size([64]) from checkpoint, th